In [1]:
import numpy as np
import pandas as pd
import pickle as pk

In [2]:
#city = 'City1'
city = 'London'

In [3]:
data = pd.read_csv("data_process/_RawData/" + city + "/POIs.csv")
quantity_of_POIS = len(data)
quantity_of_POIS

30

In [4]:
map_of_POIs = {}
index = 0
for poi in list(data['poiID']):
    map_of_POIs[poi] = index
    index = index + 1

map_of_POIs

{1: 0,
 2: 1,
 3: 2,
 4: 3,
 5: 4,
 6: 5,
 7: 6,
 8: 7,
 9: 8,
 10: 9,
 11: 10,
 12: 11,
 13: 12,
 14: 13,
 15: 14,
 16: 15,
 17: 16,
 18: 17,
 19: 18,
 20: 19,
 21: 20,
 22: 21,
 23: 22,
 24: 23,
 25: 24,
 26: 25,
 27: 26,
 28: 27,
 29: 28,
 30: 29}

In [5]:
data = pd.read_csv("data_process/_RawData/" + city + "/touristsVisits.csv")
#data = data.head(10)
data.head()


photoID         userID   dateTaken  poiID   poiTheme  seqID
0        1  100153087@N08  1523635910      8     Museum      2
1        2  100153087@N08  1523640111      8     Museum      2
2        3  100228151@N03  1498927024      3  Transport      3
3        4  100228151@N03  1498927504      3  Transport      3
4        5  100243935@N07  1542141560      6   Shopping      5

In [6]:
quant = len(data)
quant

48702

In [7]:
len(data['userID'].unique())

2226

In [8]:
global_adj = np.matrix(np.zeros(shape=(quantity_of_POIS,quantity_of_POIS)))

local_adj = dict.fromkeys(list(data['userID']), None)
for item in list(data['userID']):
    local_adj[item] = np.matrix(np.zeros(shape=(quantity_of_POIS,quantity_of_POIS)))
#local_adj = dict.fromkeys(list(data['userID']),np.matrix(np.zeros(shape=(quantity_of_POIS,quantity_of_POIS))))
#local_adj

In [9]:
#local_adj

In [10]:
data

photoID         userID   dateTaken  poiID   poiTheme  seqID
0            1  100153087@N08  1523635910      8     Museum      2
1            2  100153087@N08  1523640111      8     Museum      2
2            3  100228151@N03  1498927024      3  Transport      3
3            4  100228151@N03  1498927504      3  Transport      3
4            5  100243935@N07  1542141560      6   Shopping      5
...        ...            ...         ...    ...        ...    ...
48697    48698   99941383@N00  1501962906      6   Shopping  13748
48698    48699   99941383@N00  1501962932      6   Shopping  13748
48699    48700   99941383@N00  1501962936      6   Shopping  13748
48700    48701   99941383@N00  1504974835     16   Precinct  13750
48701    48702   99941383@N00  1504978460     16   Precinct  13750

[48702 rows x 6 columns]

In [11]:
unique_seqID = list(data['seqID'].unique())

In [12]:
sequences_dict = {}
#biggest_seq = data['seqID'].max()

for seq in unique_seqID:
    sequence = list(data[data['seqID'] == seq]['poiID'].unique())
    id_user = data[data['seqID'] == seq]['userID'].unique()[0]
    
    if id_user in sequences_dict and len(sequence) > len(sequences_dict[id_user]):
        sequences_dict[id_user] = sequence
        
    elif id_user not in sequences_dict:
        sequences_dict[id_user] = sequence
        
    

In [13]:
sequences_dict

{'100153087@N08': [8],
 '100228151@N03': [3],
 '100243935@N07': [6],
 '100251963@N05': [12],
 '10028574@N02': [1],
 '100404341@N06': [5],
 '100470389@N06': [3],
 '100595443@N07': [5],
 '10073165@N03': [11],
 '10076455@N04': [19],
 '100940221@N03': [26],
 '100978997@N07': [5, 26],
 '100987139@N04': [2],
 '100991133@N03': [5],
 '101053609@N05': [28],
 '101090910@N07': [16],
 '101133171@N06': [26],
 '101212512@N07': [16, 22, 1, 3],
 '10135721@N02': [5],
 '101419012@N05': [3],
 '101463652@N02': [5],
 '10147029@N08': [25],
 '101485105@N07': [28],
 '101599161@N06': [3],
 '101677044@N07': [26],
 '101767795@N08': [5],
 '101830676@N05': [26],
 '101875654@N07': [3],
 '10188381@N08': [2, 6],
 '10210996@N04': [16],
 '10221816@N05': [18],
 '102284959@N03': [3],
 '10246637@N04': [30],
 '10257132@N08': [11, 3, 6],
 '10288162@N07': [16, 3],
 '103033299@N08': [6],
 '10310451@N05': [17],
 '10338784@N02': [26],
 '103429480@N03': [3],
 '103451433@N02': [3],
 '103560756@N06': [11],
 '103577703@N04': [21],


In [14]:
#sequences_dict
with open("data_process/" + city +  "/sequence","wb") as file:
    pk.dump(sequences_dict, file)

In [15]:
#data = data.groupby('seqID')
for item in sequences_dict:
    if(len(sequences_dict[item]) > 1):
        for poi in range(0, len(sequences_dict[item])-1):
            user_id = item
            
            i = map_of_POIs[sequences_dict[item][poi]]
            j = map_of_POIs[sequences_dict[item][poi + 1]]
            
            local_adj[user_id][i,j] = local_adj[user_id][i,j] + 1
            local_adj[user_id][j,i] = local_adj[user_id][j,i] + 1

            global_adj[i,j] = global_adj[i,j] + 1
            global_adj[j,i] = global_adj[j,i] + 1 

In [16]:
#global_adj

In [17]:
with open("data_process/" + city + "/local","wb") as file:
    pk.dump(local_adj, file)
with open("data_process/" + city + "/global","wb") as file:
    pk.dump(global_adj, file)

In [18]:
file = open('data_process/' + city + '/global', 'rb')
d = pk.load(file)

In [19]:
d

matrix([[ 0.,  1., 11.,  2.,  9.,  4.,  1.,  0.,  0.,  0.,  1.,  0.,  0.,
          1.,  0., 11.,  1.,  0.,  2.,  0.,  0., 15.,  0.,  0.,  0.,  2.,
          0.,  6.,  0.,  4.],
        [ 1.,  0.,  2.,  0., 12.,  6.,  0.,  0.,  0.,  3.,  2.,  0.,  0.,
          0.,  0.,  0.,  7.,  0.,  1.,  0.,  1.,  0.,  0.,  0.,  1.,  6.,
          0.,  6.,  1.,  0.],
        [11.,  2.,  0.,  0.,  7., 10.,  0.,  1.,  0.,  1., 18.,  0.,  0.,
          0.,  0.,  8.,  2.,  7., 21.,  0.,  1.,  2.,  0.,  2.,  0.,  5.,
          0., 14.,  0.,  1.],
        [ 2.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  1.,  0.,  0.,
          2.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  0.,  1.,  0.,
          0.,  0.,  0.,  0.],
        [ 9., 12.,  7.,  0.,  0., 26.,  1.,  1.,  0.,  4.,  4.,  0.,  0.,
          0.,  0., 41.,  8.,  0.,  4.,  0.,  1.,  7.,  0.,  1.,  2.,  5.,
          0.,  7.,  0., 14.],
        [ 4.,  6., 10.,  0., 26.,  0.,  1.,  1.,  0.,  1.,  1.,  0.,  0.,
          1.,  0.,  6.,  8.,  0.,  2

In [20]:
file = open('data_process/' + city + '/local', 'rb')
d = pk.load(file)

In [21]:
d

{'100153087@N08': matrix([[0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
          0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.],
         [0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
          0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.],
         [0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
          0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.],
         [0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
          0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.],
         [0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
          0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.],
         [0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
          0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.],
         [0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
          0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0